In [2]:
# Phase 1 - Day 1: Data Inventory & Sanity Checks
# SQL Injection Detection - Learning Over Memorization

import pandas as pd
import numpy as np
import warnings
warnings.filterwarnings('ignore')

# Display settings
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', 100)

print("=" * 80)
print("PHASE 1 - DAY 1: DATA INVENTORY & QUICK SANITY CHECKS")
print("=" * 80)
print("\n Step 1: Loading Dataset with Encoding Detection...")

# Load your dataset (adjust path as needed)
dataset_path = '../data/raw/SQL_Injection_Detection_Dataset[IEEE].csv'

# Try multiple encodings
encodings_to_try = ['utf-8', 'latin-1', 'iso-8859-1', 'cp1252', 'utf-16']

df = None
successful_encoding = None

for encoding in encodings_to_try:
    try:
        print(f"\n Trying encoding: {encoding}")
        df = pd.read_csv(dataset_path, encoding=encoding)
        successful_encoding = encoding
        print(f" Successfully loaded with encoding: {encoding}")
        break
    except UnicodeDecodeError as e:
        print(f" Failed with {encoding}: {str(e)[:100]}")
    except Exception as e:
        print(f" Error with {encoding}: {str(e)[:100]}")

if df is not None:
    print("\n" + "=" * 80)
    print(f" DATASET LOADED SUCCESSFULLY WITH ENCODING: {successful_encoding.upper()}")
    print("=" * 80)
    
    print(f"\n Total rows: {len(df):,}")
    print(f" Total columns: {len(df.columns)}")
    
    # Display first few rows
    print("\n First 5 rows:")
    display(df.head())
    
    # Basic info
    print("\n Dataset Info:")
    print(df.info())
    
    # Column names and types
    print("\n Column Names and Data Types:")
    for col in df.columns:
        print(f"  • {col}: {df[col].dtype}")
    
    # Shape
    print(f"\n Dataset Shape: {df.shape}")
    
    # Memory usage
    print(f"\n Memory Usage: {df.memory_usage(deep=True).sum() / 1024**2:.2f} MB")
    
    # Check for completely empty columns
    empty_cols = df.columns[df.isnull().all()].tolist()
    if empty_cols:
        print(f"\n Completely empty columns found: {empty_cols}")
    else:
        print("\n No completely empty columns found")
        
else:
    print("\n CRITICAL ERROR: Could not load dataset with any encoding!")
    print("Please check:")
    print("  1. File path is correct")
    print("  2. File is not corrupted")
    print("  3. File is actually a CSV file")


PHASE 1 - DAY 1: DATA INVENTORY & QUICK SANITY CHECKS

 Step 1: Loading Dataset with Encoding Detection...

 Trying encoding: utf-8
 Failed with utf-8: 'utf-8' codec can't decode byte 0xb8 in position 3566: invalid start byte

 Trying encoding: latin-1
 Successfully loaded with encoding: latin-1

 DATASET LOADED SUCCESSFULLY WITH ENCODING: LATIN-1

 Total rows: 244,111
 Total columns: 3

 First 5 rows:


Query  \
0                                                                    " or pg_sleep  (  __TIME__  )  --   
1           create user name identified by pass123 temporary tablespace temp default tablespace users;   
2   AND 1  =  utl_inaddr.get_host_address   (    (   SELECT DISTINCT  (  table_name  )   FROM   (  ...   
3            select * from users where id  =  '1' or @ @1  =  1 union select 1,version  (    )   -- 1'   
4                 select * from users where id  =  1 or 1#"  (   union select 1,version  (    )   -- 1   

  Label  Unnamed: 2  
0     1         NaN  
1     1         NaN  
2     1         NaN  
3     1         NaN  
4     1         NaN


 Dataset Info:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 244111 entries, 0 to 244110
Data columns (total 3 columns):
 #   Column      Non-Null Count   Dtype  
---  ------      --------------   -----  
 0   Query       244106 non-null  object 
 1   Label       244087 non-null  object 
 2   Unnamed: 2  2 non-null       float64
dtypes: float64(1), object(2)
memory usage: 5.6+ MB
None

 Column Names and Data Types:
  • Query: object
  • Label: object
  • Unnamed: 2: float64

 Dataset Shape: (244111, 3)

 Memory Usage: 106.90 MB

 No completely empty columns found


In [4]:
print("=" * 80)
print("STEP 2: INITIAL DATA QUALITY ASSESSMENT")
print("=" * 80)

# Create data inventory log
data_inventory = {
    'Total Rows': len(df),
    'Total Columns': len(df.columns),
    'Encoding Used': 'latin-1',
    'Memory Usage (MB)': f"{df.memory_usage(deep=True).sum() / 1024**2:.2f}",
    'Expected Rows': '~148,000 (mentioned in project)',
    'Actual Rows': f'{len(df):,}'
}

print("\n DATA INVENTORY:")
for key, value in data_inventory.items():
    print(f"  • {key}: {value}")

print("\n" + "=" * 80)
print("CRITICAL ISSUES IDENTIFIED:")
print("=" * 80)

# Issue 1: Extra column
print("\n1️ ISSUE: Unexpected 'Unnamed: 2' column")
print(f"   - Non-null values: {df['Unnamed: 2'].notna().sum()}")
print(f"   - Null values: {df['Unnamed: 2'].isna().sum()}")
print(f"   - Unique values: {df['Unnamed: 2'].dropna().unique()}")
print("    This column appears to be mostly empty (only 2 non-null values)")

# Issue 2: Missing values in main columns
print("\n2️ ISSUE: Missing values in critical columns")
print(f"   - Query column missing: {df['Query'].isna().sum()} rows ({df['Query'].isna().sum()/len(df)*100:.2f}%)")
print(f"   - Label column missing: {df['Label'].isna().sum()} rows ({df['Label'].isna().sum()/len(df)*100:.2f}%)")

# Issue 3: Label is object type (should be numeric)
print("\n3️ ISSUE: Label column is 'object' type (should be numeric)")
print(f"   - Unique values in Label: {df['Label'].dropna().unique()[:20]}")
print(f"   - Value counts:")
print(df['Label'].value_counts(dropna=False))

# Issue 4: Dataset size mismatch
print("\n4️ ISSUE: Dataset size mismatch")
print(f"   - Expected: ~148,000 rows")
print(f"   - Actual: {len(df):,} rows")
print(f"   - Difference: {len(df) - 148000:,} rows ({(len(df) - 148000)/148000*100:+.1f}%)")

print("\n" + "=" * 80)
print(" DETAILED COLUMN ANALYSIS:")
print("=" * 80)

for col in df.columns:
    print(f"\n Column: {col}")
    print(f"   - Data type: {df[col].dtype}")
    print(f"   - Non-null: {df[col].notna().sum():,} ({df[col].notna().sum()/len(df)*100:.2f}%)")
    print(f"   - Null: {df[col].isna().sum():,} ({df[col].isna().sum()/len(df)*100:.2f}%)")
    print(f"   - Unique values: {df[col].nunique()}")
    
    if col == 'Query':
        # Show sample queries
        print(f"   - Sample queries (first 3 non-null):")
        for i, query in enumerate(df['Query'].dropna().head(3), 1):
            print(f"      {i}. {query[:80]}...")
    
    if col == 'Label':
        print(f"   - Value distribution:")
        print(df[col].value_counts(dropna=False).to_string(max_rows=10))

print("\n" + "=" * 80)
print(" INITIAL ASSESSMENT COMPLETE")
print("=" * 80)
print("\n NEXT STEPS REQUIRED:")
print("   1. Remove 'Unnamed: 2' column (almost completely empty)")
print("   2. Handle missing values in Query and Label columns")
print("   3. Convert Label column to numeric (0/1)")
print("   4. Investigate dataset size discrepancy")
print("   5. Check for duplicate rows")


STEP 2: INITIAL DATA QUALITY ASSESSMENT

 DATA INVENTORY:
  • Total Rows: 244111
  • Total Columns: 3
  • Encoding Used: latin-1
  • Memory Usage (MB): 106.90
  • Expected Rows: ~148,000 (mentioned in project)
  • Actual Rows: 244,111

CRITICAL ISSUES IDENTIFIED:

1️ ISSUE: Unexpected 'Unnamed: 2' column
   - Non-null values: 2
   - Null values: 244109
   - Unique values: [0.]
    This column appears to be mostly empty (only 2 non-null values)

2️ ISSUE: Missing values in critical columns
   - Query column missing: 5 rows (0.00%)
   - Label column missing: 24 rows (0.01%)

3️ ISSUE: Label column is 'object' type (should be numeric)
   - Unique values in Label: ['1' '0' ' exec xp_regread' "waitfor delay '0:0:__TIME__'--"
 " if not   (    (   select serverproperty  (  'isintegratedsecurityonly'   )    )    <> 1  )   waitfor delay '0:0:2' --"
 " or '1'  =  '1'" ' --' ' grant resource to name' 's'
 ' EXEC SelectAllCustomers'
 ' /*Select all the columns of all the records in the Customers t

In [5]:
print("=" * 80)
print("STEP 3: INVESTIGATE LABEL COLUMN CONTAMINATION")
print("=" * 80)

# The Label column has SQL queries mixed in - this is CRITICAL contamination!
print("\n🚨 CRITICAL FINDING: Label column contains SQL queries instead of 0/1 labels!")
print("\nInvestigating the contaminated rows...\n")

# Find rows where Label is NOT '0' or '1'
valid_labels = ['0', '1']
contaminated_mask = ~df['Label'].isin(valid_labels) & df['Label'].notna()
contaminated_rows = df[contaminated_mask].copy()

print(f"📊 Contaminated rows found: {len(contaminated_rows)}")
print(f"   Percentage of dataset: {len(contaminated_rows)/len(df)*100:.3f}%")

print("\n📋 Sample of contaminated rows:")
print("=" * 80)
display(contaminated_rows.head(10))

print("\n🔍 Analyzing contamination pattern:")
print(f"   - Total contaminated: {len(contaminated_rows)}")
print(f"   - Unique contaminated labels: {df[contaminated_mask]['Label'].nunique()}")
print("\n   Contaminated label values:")
for label in df[contaminated_mask]['Label'].unique():
    count = (df['Label'] == label).sum()
    print(f"      • '{label[:50]}...': {count} rows")

# Check if these contaminated rows have NULL in Query column
print("\n🔍 Cross-checking Query column for contaminated rows:")
contaminated_with_null_query = contaminated_rows['Query'].isna().sum()
contaminated_with_valid_query = contaminated_rows['Query'].notna().sum()
print(f"   - Rows with NULL Query: {contaminated_with_null_query}")
print(f"   - Rows with valid Query: {contaminated_with_valid_query}")

if contaminated_with_valid_query > 0:
    print("\n   Sample rows with both Query AND contaminated Label:")
    display(contaminated_rows[contaminated_rows['Query'].notna()].head(3))

# Check for duplicate rows
print("\n" + "=" * 80)
print("STEP 4: CHECK FOR DUPLICATE ROWS")
print("=" * 80)

duplicates_all = df.duplicated(keep=False).sum()
duplicates_first = df.duplicated(keep='first').sum()
print(f"\n📊 Duplicate analysis:")
print(f"   - Total duplicate rows (all occurrences): {duplicates_all:,}")
print(f"   - Duplicate rows to remove (keep='first'): {duplicates_first:,}")
print(f"   - Percentage duplicates: {duplicates_first/len(df)*100:.2f}%")

if duplicates_first > 0:
    print(f"\n   Sample duplicate rows:")
    dup_sample = df[df.duplicated(keep='first')].head(3)
    display(dup_sample)

print("\n" + "=" * 80)
print("📋 DATA CLEANING STRATEGY")
print("=" * 80)
print("\n✅ STEP-BY-STEP CLEANING PLAN:")
print("\n1. Remove 'Unnamed: 2' column (99.999% empty)")
print(f"   - Will remove 1 column")

print("\n2. Remove contaminated Label rows")
print(f"   - Will remove {len(contaminated_rows):,} rows with SQL queries in Label column")

print("\n3. Remove rows with missing Query or Label")
print(f"   - Query missing: {df['Query'].isna().sum()} rows")
print(f"   - Label missing: {df['Label'].isna().sum()} rows")
print(f"   - Total to remove: {(df['Query'].isna() | df['Label'].isna()).sum()} rows")

print("\n4. Remove duplicate rows")
print(f"   - Will remove {duplicates_first:,} duplicate rows")

print("\n5. Convert Label to numeric (0/1)")

# Calculate final expected rows
rows_to_remove = len(contaminated_rows) + (df['Query'].isna() | df['Label'].isna()).sum() + duplicates_first
expected_final_rows = len(df) - rows_to_remove

print("\n" + "=" * 80)
print("📊 EXPECTED CLEANING RESULTS:")
print("=" * 80)
print(f"   Starting rows: {len(df):,}")
print(f"   Rows to remove: {rows_to_remove:,}")
print(f"   Expected final rows: {expected_final_rows:,}")
print(f"   Expected reduction: {rows_to_remove/len(df)*100:.2f}%")

print("\n⚠️ WAITING FOR YOUR CONFIRMATION TO PROCEED WITH CLEANING")


STEP 3: INVESTIGATE LABEL COLUMN CONTAMINATION

🚨 CRITICAL FINDING: Label column contains SQL queries instead of 0/1 labels!

Investigating the contaminated rows...

📊 Contaminated rows found: 19
   Percentage of dataset: 0.008%

📋 Sample of contaminated rows:


Query  \
213434                           NaN   
213599                           NaN   
213694                           NaN   
213901                           NaN   
213950          x' and email is NULL   
213983  x' AND members.email IS NULL   
232495         grant connect to name   
232500                           NaN   
233096    SELECT * FROM Customers GO   
233100        SELECT * FROM Products   

                                                                                                      Label  \
213434                                                                                      exec xp_regread   
213599                                                                       waitfor delay '0:0:__TIME__'--   
213694   if not   (    (   select serverproperty  (  'isintegratedsecurityonly'   )    )    <> 1  )   wa...   
213901                                                                                       or '1'  =  '1'   
213950                                                                                                   --   
213983                                                                                                   --   
232495                                                                               grant resource to name   
232500                                                                                                    s   
233096                                                                              EXEC SelectAllCustomers   
233100                                /*Select all the columns of all the records in the Customers table:*/   

        Unnamed: 2  
213434         NaN  
213599         NaN  
213694         NaN  
213901         NaN  
213950         NaN  
213983         NaN  
232495         NaN  
232500         NaN  
233096         0.0  
233100         NaN


🔍 Analyzing contamination pattern:
   - Total contaminated: 19
   - Unique contaminated labels: 18

   Contaminated label values:
      • ' exec xp_regread...': 1 rows
      • 'waitfor delay '0:0:__TIME__'--...': 1 rows
      • ' if not   (    (   select serverproperty  (  'isin...': 1 rows
      • ' or '1'  =  '1'...': 1 rows
      • ' --...': 2 rows
      • ' grant resource to name...': 1 rows
      • 's...': 1 rows
      • ' EXEC SelectAllCustomers...': 1 rows
      • ' /*Select all the columns of all the records in th...': 1 rows
      • '*/...': 1 rows
      • ' CREATE VIEW [Products Above Average Price] AS...': 1 rows
      • ' CREATE OR REPLACE VIEW view_name AS...': 1 rows
      • ' CREATE PROCEDURE SelectAllCustomers AS...': 1 rows
      • '  EXEC SelectAllCustomers...': 1 rows
      • ' SELECT * FROM Customers...': 1 rows
      • 'SELECT SUM ( Quantity ) ...': 1 rows
      • ' SELECT column_name ( s ) ...': 1 rows
      • ' SELECT City FROM Customers...': 1 rows

🔍 Cross-che

Query                    Label  Unnamed: 2
213950          x' and email is NULL                       --         NaN
213983  x' AND members.email IS NULL                       --         NaN
232495         grant connect to name   grant resource to name         NaN


STEP 4: CHECK FOR DUPLICATE ROWS

📊 Duplicate analysis:
   - Total duplicate rows (all occurrences): 61,807
   - Duplicate rows to remove (keep='first'): 31,159
   - Percentage duplicates: 12.76%

   Sample duplicate rows:


Query Label  Unnamed: 2
346     or 3  =  3 --     1         NaN
357     or 1  =  1 --     1         NaN
11746         3.82E+15     0         NaN


📋 DATA CLEANING STRATEGY

✅ STEP-BY-STEP CLEANING PLAN:

1. Remove 'Unnamed: 2' column (99.999% empty)
   - Will remove 1 column

2. Remove contaminated Label rows
   - Will remove 19 rows with SQL queries in Label column

3. Remove rows with missing Query or Label
   - Query missing: 5 rows
   - Label missing: 24 rows
   - Total to remove: 29 rows

4. Remove duplicate rows
   - Will remove 31,159 duplicate rows

5. Convert Label to numeric (0/1)

📊 EXPECTED CLEANING RESULTS:
   Starting rows: 244,111
   Rows to remove: 31,207
   Expected final rows: 212,904
   Expected reduction: 12.78%

⚠️ WAITING FOR YOUR CONFIRMATION TO PROCEED WITH CLEANING


In [8]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.express as px

print("=" * 80)
print("STEP 5: DATA CLEANING EXECUTION")
print("=" * 80)

# Create a log to track all removed rows
cleaning_log = []

# Store original dataset info
original_shape = df.shape
original_rows = len(df)

print(f"\nOriginal dataset: {original_rows:,} rows, {df.shape[1]} columns")

# Step 1: Remove 'Unnamed: 2' column
print("\n" + "-" * 80)
print("Step 1: Removing 'Unnamed: 2' column")
df_clean = df.drop(columns=['Unnamed: 2'])
print(f"Result: Column removed. New shape: {df_clean.shape}")

# Step 2: Remove contaminated Label rows
print("\n" + "-" * 80)
print("Step 2: Removing contaminated Label rows")
valid_labels = ['0', '1']
contaminated_mask = ~df_clean['Label'].isin(valid_labels) & df_clean['Label'].notna()
contaminated_count = contaminated_mask.sum()

# Log contaminated rows
contaminated_rows_log = df_clean[contaminated_mask][['Query', 'Label']].copy()
contaminated_rows_log['Removal_Reason'] = 'Contaminated_Label'
cleaning_log.append(contaminated_rows_log)

df_clean = df_clean[~contaminated_mask]
print(f"Result: Removed {contaminated_count} rows with contaminated labels")
print(f"Remaining rows: {len(df_clean):,}")

# Step 3: Remove rows with missing Query or Label
print("\n" + "-" * 80)
print("Step 3: Removing rows with missing Query or Label")
missing_query = df_clean['Query'].isna().sum()
missing_label = df_clean['Label'].isna().sum()
missing_mask = df_clean['Query'].isna() | df_clean['Label'].isna()
missing_count = missing_mask.sum()

# Log missing rows
missing_rows_log = df_clean[missing_mask][['Query', 'Label']].copy()
missing_rows_log['Removal_Reason'] = 'Missing_Values'
cleaning_log.append(missing_rows_log)

df_clean = df_clean[~missing_mask]
print(f"Result: Removed {missing_count} rows")
print(f"  - Missing Query: {missing_query}")
print(f"  - Missing Label: {missing_label}")
print(f"Remaining rows: {len(df_clean):,}")

# Step 4: Remove duplicate rows
print("\n" + "-" * 80)
print("Step 4: Removing duplicate rows")
duplicates_before = df_clean.duplicated(keep='first').sum()

# Log duplicate rows
duplicate_rows_log = df_clean[df_clean.duplicated(keep='first')][['Query', 'Label']].copy()
duplicate_rows_log['Removal_Reason'] = 'Duplicate'
cleaning_log.append(duplicate_rows_log)

df_clean = df_clean.drop_duplicates(keep='first')
print(f"Result: Removed {duplicates_before:,} duplicate rows")
print(f"Remaining rows: {len(df_clean):,}")

# Step 5: Convert Label to numeric
print("\n" + "-" * 80)
print("Step 5: Converting Label column to numeric")
df_clean['Label'] = df_clean['Label'].astype(int)
print(f"Result: Label column converted to int type")
print(f"Unique values: {df_clean['Label'].unique()}")

# Final statistics
print("\n" + "=" * 80)
print("CLEANING SUMMARY")
print("=" * 80)
print(f"Original rows:        {original_rows:,}")
print(f"Contaminated removed: {contaminated_count:,}")
print(f"Missing removed:      {missing_count:,}")
print(f"Duplicates removed:   {duplicates_before:,}")
print(f"Total removed:        {original_rows - len(df_clean):,}")
print(f"Final clean rows:     {len(df_clean):,}")
print(f"Reduction:            {(original_rows - len(df_clean))/original_rows*100:.2f}%")

# Create removal log dataframe
removal_log = pd.concat(cleaning_log, ignore_index=True)
print(f"\nRemoval log created: {len(removal_log):,} entries")

# Create Plotly visualizations
print("\n" + "=" * 80)
print("GENERATING INTERACTIVE VISUALIZATIONS")
print("=" * 80)

# Prepare data for visualizations
stages = ['Original', 'After<br>Contamination', 'After<br>Missing', 'After<br>Duplicates']
row_counts = [
    original_rows,
    original_rows - contaminated_count,
    original_rows - contaminated_count - missing_count,
    len(df_clean)
]

# Create subplots
fig = make_subplots(
    rows=1, cols=2,
    subplot_titles=('Data Cleaning Process - Row Count Changes', 
                    'Data Removal Breakdown'),
    specs=[[{"type": "bar"}, {"type": "pie"}]]
)

# Chart 1: Bar chart showing cleaning stages
fig.add_trace(
    go.Bar(
        x=stages,
        y=row_counts,
        text=[f'{v:,}' for v in row_counts],
        textposition='outside',
        marker=dict(
            color=['#3498db', '#2ecc71', '#f39c12', '#27ae60'],
            line=dict(color='white', width=2)
        ),
        showlegend=False
    ),
    row=1, col=1
)

# Chart 2: Pie chart showing removal breakdown
removal_categories = ['Contaminated', 'Missing', 'Duplicates', 'Kept']
removal_counts = [contaminated_count, missing_count, duplicates_before, len(df_clean)]
colors = ['#e74c3c', '#e67e22', '#f39c12', '#27ae60']

fig.add_trace(
    go.Pie(
        labels=removal_categories,
        values=removal_counts,
        marker=dict(colors=colors),
        textinfo='label+percent',
        hovertemplate='<b>%{label}</b><br>Count: %{value:,}<br>Percentage: %{percent}<extra></extra>'
    ),
    row=1, col=2
)

# Update layout
fig.update_xaxes(title_text="Cleaning Stage", row=1, col=1)
fig.update_yaxes(title_text="Number of Rows", row=1, col=1)

fig.update_layout(
    height=500,
    showlegend=False,
    title_text="Phase 1: Data Cleaning Visualization",
    title_x=0.5,
    title_font=dict(size=18, family='Arial Black')
)

fig.show()



STEP 5: DATA CLEANING EXECUTION

Original dataset: 244,111 rows, 3 columns

--------------------------------------------------------------------------------
Step 1: Removing 'Unnamed: 2' column
Result: Column removed. New shape: (244111, 2)

--------------------------------------------------------------------------------
Step 2: Removing contaminated Label rows
Result: Removed 19 rows with contaminated labels
Remaining rows: 244,092

--------------------------------------------------------------------------------
Step 3: Removing rows with missing Query or Label
Result: Removed 24 rows
  - Missing Query: 0
  - Missing Label: 24
Remaining rows: 244,068

--------------------------------------------------------------------------------
Step 4: Removing duplicate rows
Result: Removed 31,159 duplicate rows
Remaining rows: 212,909

--------------------------------------------------------------------------------
Step 5: Converting Label column to numeric
Result: Label column converted to int t

In [9]:
print("=" * 80)
print("STEP 6: CLASS BALANCE ANALYSIS")
print("=" * 80)

# Get class distribution
class_counts = df_clean['Label'].value_counts().sort_index()
total_samples = len(df_clean)

print("\nClass Distribution:")
print("-" * 40)
for label in class_counts.index:
    count = class_counts[label]
    percentage = (count / total_samples) * 100
    label_name = "Normal (0)" if label == 0 else "Malicious (1)"
    print(f"{label_name}: {count:,} samples ({percentage:.2f}%)")

# Calculate class imbalance ratio
malicious_count = class_counts[1]
normal_count = class_counts[0]
imbalance_ratio = malicious_count / normal_count

print("\n" + "-" * 40)
print(f"Class Imbalance Ratio (Malicious:Normal): {imbalance_ratio:.4f}")
print(f"Or approximately: {malicious_count/normal_count:.2f}:1")

# Calculate class weights for model training
from sklearn.utils.class_weight import compute_class_weight

class_weights = compute_class_weight(
    class_weight='balanced',
    classes=np.array([0, 1]),
    y=df_clean['Label']
)

class_weight_dict = {0: class_weights[0], 1: class_weights[1]}

print("\nComputed Class Weights for Training:")
print("-" * 40)
print(f"Normal (0): {class_weights[0]:.4f}")
print(f"Malicious (1): {class_weights[1]:.4f}")

# Query length statistics
df_clean['query_length'] = df_clean['Query'].str.len()

print("\n" + "=" * 80)
print("QUERY LENGTH STATISTICS")
print("=" * 80)

length_stats = df_clean.groupby('Label')['query_length'].describe()
print("\nQuery Length Statistics by Class:")
print(length_stats)

# Overall statistics
print("\nOverall Query Length Statistics:")
print("-" * 40)
print(f"Mean length: {df_clean['query_length'].mean():.2f} characters")
print(f"Median length: {df_clean['query_length'].median():.2f} characters")
print(f"Min length: {df_clean['query_length'].min()} characters")
print(f"Max length: {df_clean['query_length'].max()} characters")
print(f"Std deviation: {df_clean['query_length'].std():.2f} characters")

# Create interactive visualizations
print("\n" + "=" * 80)
print("GENERATING CLASS BALANCE VISUALIZATIONS")
print("=" * 80)

# Create subplots for class analysis
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        'Class Distribution',
        'Class Imbalance Ratio',
        'Query Length Distribution by Class',
        'Query Length Box Plot by Class'
    ),
    specs=[
        [{"type": "bar"}, {"type": "indicator"}],
        [{"type": "histogram"}, {"type": "box"}]
    ],
    row_heights=[0.4, 0.6]
)

# Chart 1: Class distribution bar chart
fig.add_trace(
    go.Bar(
        x=['Normal (0)', 'Malicious (1)'],
        y=[normal_count, malicious_count],
        text=[f'{normal_count:,}<br>({normal_count/total_samples*100:.1f}%)',
              f'{malicious_count:,}<br>({malicious_count/total_samples*100:.1f}%)'],
        textposition='outside',
        marker=dict(color=['#3498db', '#e74c3c']),
        showlegend=False
    ),
    row=1, col=1
)

# Chart 2: Imbalance ratio indicator
fig.add_trace(
    go.Indicator(
        mode="number+delta",
        value=imbalance_ratio,
        title={'text': f"Malicious:Normal<br>Ratio"},
        number={'suffix': ":1", 'font': {'size': 40}},
        delta={'reference': 1, 'relative': False},
        domain={'x': [0, 1], 'y': [0, 1]}
    ),
    row=1, col=2
)

# Chart 3: Query length distribution histogram
for label in [0, 1]:
    label_name = "Normal" if label == 0 else "Malicious"
    color = '#3498db' if label == 0 else '#e74c3c'
    
    fig.add_trace(
        go.Histogram(
            x=df_clean[df_clean['Label'] == label]['query_length'],
            name=label_name,
            opacity=0.7,
            marker=dict(color=color),
            nbinsx=50
        ),
        row=2, col=1
    )

# Chart 4: Query length box plot
for label in [0, 1]:
    label_name = "Normal" if label == 0 else "Malicious"
    color = '#3498db' if label == 0 else '#e74c3c'
    
    fig.add_trace(
        go.Box(
            y=df_clean[df_clean['Label'] == label]['query_length'],
            name=label_name,
            marker=dict(color=color),
            boxmean='sd'
        ),
        row=2, col=2
    )

# Update layout
fig.update_xaxes(title_text="Class", row=1, col=1)
fig.update_yaxes(title_text="Number of Samples", row=1, col=1)
fig.update_xaxes(title_text="Query Length (characters)", row=2, col=1)
fig.update_yaxes(title_text="Frequency", row=2, col=1)
fig.update_xaxes(title_text="Class", row=2, col=2)
fig.update_yaxes(title_text="Query Length (characters)", row=2, col=2)

fig.update_layout(
    height=800,
    title_text="Phase 1: Class Balance and Query Analysis",
    title_x=0.5,
    title_font=dict(size=18),
    showlegend=True
)

fig.show()

print("\nClass balance visualizations generated successfully.")

# Summary for documentation
print("\n" + "=" * 80)
print("PHASE 1 DATA QUALITY SUMMARY")
print("=" * 80)
print(f"\nFinal Clean Dataset:")
print(f"  Total samples: {len(df_clean):,}")
print(f"  Normal queries: {normal_count:,} ({normal_count/total_samples*100:.2f}%)")
print(f"  Malicious queries: {malicious_count:,} ({malicious_count/total_samples*100:.2f}%)")
print(f"  Class imbalance ratio: {imbalance_ratio:.4f}")
print(f"  Unique queries: {df_clean['Query'].nunique():,}")
print(f"\nData Quality Issues Resolved:")
print(f"  - Encoding: latin-1 used (UTF-8 failed)")
print(f"  - Contaminated labels: 19 rows removed")
print(f"  - Missing values: 24 rows removed")
print(f"  - Duplicates: 31,159 rows removed")
print(f"  - Total reduction: 12.78%")


STEP 6: CLASS BALANCE ANALYSIS

Class Distribution:
----------------------------------------
Normal (0): 87,178 samples (40.95%)
Malicious (1): 125,731 samples (59.05%)

----------------------------------------
Class Imbalance Ratio (Malicious:Normal): 1.4422
Or approximately: 1.44:1

Computed Class Weights for Training:
----------------------------------------
Normal (0): 1.2211
Malicious (1): 0.8467

QUERY LENGTH STATISTICS

Query Length Statistics by Class:
          count        mean         std  min    25%    50%    75%     max
Label                                                                    
0       87178.0  322.429696  300.136459  1.0   43.0  241.0  575.0  5370.0
1      125731.0  411.815097  293.071840  1.0  139.0  361.0  659.0  1340.0

Overall Query Length Statistics:
----------------------------------------
Mean length: 375.22 characters
Median length: 317.00 characters
Min length: 1 characters
Max length: 5370 characters
Std deviation: 299.23 characters

GENERATING CL


Class balance visualizations generated successfully.

PHASE 1 DATA QUALITY SUMMARY

Final Clean Dataset:
  Total samples: 212,909
  Normal queries: 87,178 (40.95%)
  Malicious queries: 125,731 (59.05%)
  Class imbalance ratio: 1.4422
  Unique queries: 212,902

Data Quality Issues Resolved:
  - Encoding: latin-1 used (UTF-8 failed)
  - Contaminated labels: 19 rows removed
  - Missing values: 24 rows removed
  - Duplicates: 31,159 rows removed
  - Total reduction: 12.78%


In [10]:
print("=" * 80)
print("CLASS IMBALANCE ASSESSMENT")
print("=" * 80)

# Current class distribution
normal_count = 87178
malicious_count = 125731
total_samples = 212909
imbalance_ratio = 1.4422

print("\nCurrent Class Distribution:")
print("-" * 40)
print(f"Normal (0):    {normal_count:>7,} ({normal_count/total_samples*100:>5.2f}%)")
print(f"Malicious (1): {malicious_count:>7,} ({malicious_count/total_samples*100:>5.2f}%)")
print(f"\nImbalance Ratio: {imbalance_ratio:.4f}:1 (Malicious:Normal)")

# Assess imbalance severity
print("\n" + "=" * 80)
print("IMBALANCE SEVERITY ASSESSMENT")
print("=" * 80)

print("\nImbalance Categories:")
print("-" * 40)
print("  Balanced:        0.8 - 1.2 (minority is 45-55% of majority)")
print("  Slightly Imb:    1.2 - 2.0 (minority is 33-45% of majority)")
print("  Moderately Imb:  2.0 - 5.0 (minority is 17-33% of majority)")
print("  Highly Imb:      5.0 - 10.0 (minority is 9-17% of majority)")
print("  Severely Imb:    >10.0 (minority is <9% of majority)")

minority_percentage = (normal_count / malicious_count) * 100

print(f"\nYour Dataset:")
print(f"  Minority class is {minority_percentage:.1f}% of majority class")
print(f"  Classification: SLIGHTLY IMBALANCED")

print("\n" + "=" * 80)
print("RECOMMENDED ACTIONS")
print("=" * 80)

print("\nGOOD NEWS: Your 1.44:1 ratio is MANAGEABLE")
print("-" * 60)

print("\nWhy this is acceptable:")
print("  1. Ratio is close to balanced (not extreme)")
print("  2. Both classes have substantial samples:")
print(f"     - Normal: {normal_count:,} samples")
print(f"     - Malicious: {malicious_count:,} samples")
print("  3. This reflects realistic attack/normal traffic distribution")
print("  4. Deep learning models can handle this level of imbalance")

print("\nStrategy to handle this imbalance:")
print("-" * 60)
print("  PRIMARY APPROACH: Use Class Weights (Already Computed)")
print(f"    - Normal (0) weight: 1.2211")
print(f"    - Malicious (1) weight: 0.8467")
print("    - These weights will be used during CNN training")
print("    - No need for SMOTE or undersampling")

print("\n  SUPPORTING STRATEGIES:")
print("    1. Stratified train/val/test split (preserve ratio)")
print("    2. Monitor per-class metrics (Precision/Recall/F1)")
print("    3. Use appropriate evaluation metrics:")
print("       - Balanced Accuracy")
print("       - F1-Score (weighted)")
print("       - ROC-AUC")
print("       - Confusion Matrix")

print("\n  AVOID:")
print("    - Simple accuracy as primary metric")
print("    - Random sampling (use stratified)")
print("    - Ignoring class weights in model training")

# Compare with other scenarios
print("\n" + "=" * 80)
print("COMPARISON WITH OTHER IMBALANCE SCENARIOS")
print("=" * 80)

scenarios = [
    ("Fraud Detection", "1:100 to 1:1000", "Severely imbalanced - needs SMOTE/undersampling"),
    ("Your SQL Injection", "1:1.44", "Slightly imbalanced - class weights sufficient"),
    ("Medical Diagnosis", "1:10 to 1:50", "Moderately imbalanced - needs multiple techniques"),
    ("Spam Detection", "1:2 to 1:3", "Slightly imbalanced - class weights work well")
]

print("\nTypical Machine Learning Scenarios:")
print("-" * 70)
for scenario, ratio, action in scenarios:
    print(f"  {scenario:<20} | {ratio:<15} | {action}")

# Decision summary
print("\n" + "=" * 80)
print("FINAL DECISION")
print("=" * 80)

print("\nCONCLUSION: NO REBALANCING NEEDED")
print("-" * 40)
print("  Status: PROCEED with current class distribution")
print("  Method: Use computed class weights during training")
print("  Reason: Ratio (1.44:1) is within manageable range")
print("  Risk:   Low risk of majority class bias")
print("\nNext Steps:")
print("  1. Use stratified split to maintain 1.44:1 ratio in all sets")
print("  2. Apply class weights in CNN model training (Phase 4)")
print("  3. Monitor per-class performance metrics")
print("  4. Validate on balanced test set if needed")

# Visualize imbalance comparison
print("\n" + "=" * 80)
print("GENERATING IMBALANCE COMPARISON VISUALIZATION")
print("=" * 80)

# Create comparison visualization
imbalance_scenarios = [
    ('Fraud<br>Detection', 100, 'Severe'),
    ('Medical<br>Diagnosis', 20, 'Moderate'),
    ('Your SQL<br>Injection', 1.44, 'Slight'),
    ('Spam<br>Detection', 2.5, 'Slight'),
    ('Balanced<br>Dataset', 1.0, 'Balanced')
]

scenario_names = [s[0] for s in imbalance_scenarios]
ratios = [s[1] for s in imbalance_scenarios]
severity = [s[2] for s in imbalance_scenarios]

# Color code by severity
colors = []
for sev in severity:
    if sev == 'Severe':
        colors.append('#e74c3c')
    elif sev == 'Moderate':
        colors.append('#f39c12')
    elif sev == 'Slight':
        colors.append('#3498db')
    else:
        colors.append('#27ae60')

fig = go.Figure()

fig.add_trace(go.Bar(
    x=scenario_names,
    y=ratios,
    text=[f'{r:.2f}:1<br>({s})' for r, s in zip(ratios, severity)],
    textposition='outside',
    marker=dict(color=colors),
    hovertemplate='<b>%{x}</b><br>Ratio: %{y:.2f}:1<br>%{text}<extra></extra>'
))

fig.add_hline(
    y=1.44, 
    line_dash="dash", 
    line_color="red",
    annotation_text="Your Dataset (1.44:1)",
    annotation_position="right"
)

fig.update_layout(
    title="Class Imbalance Comparison Across ML Scenarios",
    xaxis_title="Scenario",
    yaxis_title="Imbalance Ratio (Majority:Minority)",
    height=500,
    yaxis_type="log",
    showlegend=False
)

fig.show()

print("\nVisualization complete.")
print("\nKEY TAKEAWAY: Your 1.44:1 ratio is among the LEAST imbalanced scenarios")
print("              in machine learning - perfectly manageable with class weights!")


CLASS IMBALANCE ASSESSMENT

Current Class Distribution:
----------------------------------------
Normal (0):     87,178 (40.95%)
Malicious (1): 125,731 (59.05%)

Imbalance Ratio: 1.4422:1 (Malicious:Normal)

IMBALANCE SEVERITY ASSESSMENT

Imbalance Categories:
----------------------------------------
  Balanced:        0.8 - 1.2 (minority is 45-55% of majority)
  Slightly Imb:    1.2 - 2.0 (minority is 33-45% of majority)
  Moderately Imb:  2.0 - 5.0 (minority is 17-33% of majority)
  Highly Imb:      5.0 - 10.0 (minority is 9-17% of majority)
  Severely Imb:    >10.0 (minority is <9% of majority)

Your Dataset:
  Minority class is 69.3% of majority class
  Classification: SLIGHTLY IMBALANCED

RECOMMENDED ACTIONS

GOOD NEWS: Your 1.44:1 ratio is MANAGEABLE
------------------------------------------------------------

Why this is acceptable:
  1. Ratio is close to balanced (not extreme)
  2. Both classes have substantial samples:
     - Normal: 87,178 samples
     - Malicious: 125,731 s


Visualization complete.

KEY TAKEAWAY: Your 1.44:1 ratio is among the LEAST imbalanced scenarios
              in machine learning - perfectly manageable with class weights!


In [11]:
import json
from datetime import datetime
import os

print("=" * 80)
print("STEP 7: SAVING CLEANED DATASET")
print("=" * 80)

# Create processed data directory if it doesn't exist
processed_dir = '../data/processed/'
os.makedirs(processed_dir, exist_ok=True)

# Save cleaned dataset
cleaned_file_path = os.path.join(processed_dir, 'cleaned_dataset.csv')
df_clean.to_csv(cleaned_file_path, index=False, encoding='utf-8')

print(f"\nCleaned dataset saved successfully!")
print(f"Location: {cleaned_file_path}")
print(f"Rows: {len(df_clean):,}")
print(f"Columns: {len(df_clean.columns)}")
print(f"File size: {os.path.getsize(cleaned_file_path) / (1024*1024):.2f} MB")

# Save removal log
removal_log_path = os.path.join(processed_dir, 'removal_log.csv')
removal_log.to_csv(removal_log_path, index=False, encoding='utf-8')
print(f"\nRemoval log saved successfully!")
print(f"Location: {removal_log_path}")
print(f"Entries: {len(removal_log):,}")

# Save class weights for later use
class_weights_path = os.path.join(processed_dir, 'class_weights.json')
class_weights_data = {
    'class_weights': class_weight_dict,
    'imbalance_ratio': float(imbalance_ratio),
    'class_distribution': {
        'normal': int(normal_count),
        'malicious': int(malicious_count)
    }
}

with open(class_weights_path, 'w') as f:
    json.dump(class_weights_data, f, indent=4)

print(f"\nClass weights saved successfully!")
print(f"Location: {class_weights_path}")

# Generate comprehensive data quality report
print("\n" + "=" * 80)
print("GENERATING DATA QUALITY REPORT")
print("=" * 80)

data_quality_report = {
    'report_metadata': {
        'generated_date': datetime.now().strftime('%Y-%m-%d %H:%M:%S'),
        'phase': 'Phase 1 - Data Preparation and Cleaning',
        'status': 'COMPLETED'
    },
    'original_dataset': {
        'total_rows': 244111,
        'total_columns': 3,
        'encoding_used': 'latin-1',
        'encoding_issue': 'UTF-8 failed, latin-1 required',
        'memory_usage_mb': 106.93
    },
    'data_quality_issues': {
        'contaminated_labels': {
            'count': 19,
            'description': 'SQL queries found in Label column instead of 0/1',
            'action': 'Removed'
        },
        'missing_values': {
            'count': 24,
            'description': 'Missing Query or Label values',
            'action': 'Removed'
        },
        'duplicates': {
            'count': 31159,
            'percentage': 12.76,
            'description': 'Duplicate Query-Label pairs',
            'action': 'Removed (kept first occurrence)'
        },
        'empty_column': {
            'name': 'Unnamed: 2',
            'non_null_count': 2,
            'description': '99.999% empty column',
            'action': 'Removed'
        }
    },
    'cleaning_summary': {
        'original_rows': 244111,
        'rows_removed': 31202,
        'final_rows': 212909,
        'reduction_percentage': 12.78
    },
    'final_dataset': {
        'total_samples': 212909,
        'unique_queries': 212902,
        'columns': ['Query', 'Label'],
        'class_distribution': {
            'normal': {
                'count': 87178,
                'percentage': 40.95
            },
            'malicious': {
                'count': 125731,
                'percentage': 59.05
            }
        },
        'class_imbalance': {
            'ratio': 1.4422,
            'classification': 'Slightly Imbalanced',
            'action_required': 'Use class weights during training',
            'class_weights': {
                'normal': 1.2211,
                'malicious': 0.8467
            }
        }
    },
    'query_statistics': {
        'overall': {
            'mean_length': 375.22,
            'median_length': 317.0,
            'min_length': 1,
            'max_length': 5370,
            'std_deviation': 299.23
        },
        'by_class': {
            'normal': {
                'mean_length': 322.43,
                'median_length': 241.0,
                'std_deviation': 300.14
            },
            'malicious': {
                'mean_length': 411.82,
                'median_length': 361.0,
                'std_deviation': 293.07
            }
        }
    },
    'recommendations': {
        'splitting_strategy': 'Stratified train/val/test split (70/15/15)',
        'class_handling': 'Apply computed class weights during CNN training',
        'evaluation_metrics': [
            'Balanced Accuracy',
            'F1-Score (weighted)',
            'ROC-AUC',
            'Per-class Precision/Recall',
            'Confusion Matrix'
        ],
        'next_steps': [
            'Perform stratified split maintaining 1.44:1 ratio',
            'Conduct exploratory data analysis',
            'Validate data quality across all splits',
            'Proceed to Phase 2: Rule-based detection'
        ]
    }
}

# Save the report
report_path = os.path.join(processed_dir, 'data_quality_report.json')
with open(report_path, 'w') as f:
    json.dump(data_quality_report, f, indent=4)

print(f"\nData quality report saved successfully!")
print(f"Location: {report_path}")

# Create summary visualization with download button
print("\n" + "=" * 80)
print("GENERATING FINAL SUMMARY VISUALIZATION")
print("=" * 80)

# Create comprehensive summary visualization
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=(
        'Cleaning Impact Overview',
        'Final Class Distribution',
        'Data Quality Issues Breakdown',
        'Query Length Comparison'
    ),
    specs=[
        [{"type": "bar"}, {"type": "pie"}],
        [{"type": "bar"}, {"type": "box"}]
    ],
    row_heights=[0.5, 0.5]
)

# Chart 1: Before/After comparison
fig.add_trace(
    go.Bar(
        x=['Original Dataset', 'After Cleaning'],
        y=[244111, 212909],
        text=['244,111', '212,909'],
        textposition='outside',
        marker=dict(color=['#e74c3c', '#27ae60']),
        showlegend=False
    ),
    row=1, col=1
)

# Chart 2: Final class distribution
fig.add_trace(
    go.Pie(
        labels=['Normal (0)', 'Malicious (1)'],
        values=[87178, 125731],
        marker=dict(colors=['#3498db', '#e74c3c']),
        textinfo='label+percent+value',
        hovertemplate='<b>%{label}</b><br>Count: %{value:,}<br>Percentage: %{percent}<extra></extra>'
    ),
    row=1, col=2
)

# Chart 3: Data quality issues
issue_names = ['Contaminated<br>Labels', 'Missing<br>Values', 'Duplicates']
issue_counts = [19, 24, 31159]

fig.add_trace(
    go.Bar(
        x=issue_names,
        y=issue_counts,
        text=[f'{v:,}' for v in issue_counts],
        textposition='outside',
        marker=dict(color=['#e74c3c', '#e67e22', '#f39c12']),
        showlegend=False
    ),
    row=2, col=1
)

# Chart 4: Query length box plot
fig.add_trace(
    go.Box(
        y=df_clean[df_clean['Label'] == 0]['query_length'],
        name='Normal',
        marker=dict(color='#3498db'),
        boxmean='sd'
    ),
    row=2, col=2
)

fig.add_trace(
    go.Box(
        y=df_clean[df_clean['Label'] == 1]['query_length'],
        name='Malicious',
        marker=dict(color='#e74c3c'),
        boxmean='sd'
    ),
    row=2, col=2
)

# Update layout with download config
fig.update_xaxes(title_text="Dataset Stage", row=1, col=1)
fig.update_yaxes(title_text="Number of Rows", row=1, col=1)
fig.update_xaxes(title_text="Issue Type", row=2, col=1)
fig.update_yaxes(title_text="Count (log scale)", row=2, col=1, type="log")
fig.update_xaxes(title_text="Class", row=2, col=2)
fig.update_yaxes(title_text="Query Length (characters)", row=2, col=2)

fig.update_layout(
    height=800,
    title_text="Phase 1: Complete Data Cleaning Summary",
    title_x=0.5,
    title_font=dict(size=18),
    showlegend=True
)

# Show with download buttons enabled
config = {
    'toImageButtonOptions': {
        'format': 'png',
        'filename': 'phase1_data_cleaning_summary',
        'height': 800,
        'width': 1400,
        'scale': 2
    },
    'displayModeBar': True,
    'displaylogo': False,
    'modeBarButtonsToAdd': ['downloadImage']
}

fig.show(config=config)

print("\nVisualization complete with download capability enabled.")

# Print file summary
print("\n" + "=" * 80)
print("PHASE 1 DELIVERABLES - FILES SAVED")
print("=" * 80)

print(f"\n1. Cleaned Dataset:")
print(f"   {cleaned_file_path}")
print(f"   {len(df_clean):,} rows, {len(df_clean.columns)} columns")

print(f"\n2. Removal Log:")
print(f"   {removal_log_path}")
print(f"   {len(removal_log):,} removed entries with reasons")

print(f"\n3. Class Weights:")
print(f"   {class_weights_path}")
print(f"   Normal: 1.2211, Malicious: 0.8467")

print(f"\n4. Data Quality Report:")
print(f"   {report_path}")
print(f"   Complete JSON report with all statistics")

print("\n" + "=" * 80)
print("PHASE 1 DAY 1-2 COMPLETED SUCCESSFULLY")
print("=" * 80)
print("\nNext Steps:")
print("  Day 3-5: Perform stratified train/val/test split")
print("  Day 6-8: Conduct exploratory data analysis")
print("  Day 9-10: Final validation and documentation")


STEP 7: SAVING CLEANED DATASET

Cleaned dataset saved successfully!
Location: ../data/processed/cleaned_dataset.csv
Rows: 212,909
Columns: 3
File size: 78.22 MB

Removal log saved successfully!
Location: ../data/processed/removal_log.csv
Entries: 31,202

Class weights saved successfully!
Location: ../data/processed/class_weights.json

GENERATING DATA QUALITY REPORT

Data quality report saved successfully!
Location: ../data/processed/data_quality_report.json

GENERATING FINAL SUMMARY VISUALIZATION



Visualization complete with download capability enabled.

PHASE 1 DELIVERABLES - FILES SAVED

1. Cleaned Dataset:
   ../data/processed/cleaned_dataset.csv
   212,909 rows, 3 columns

2. Removal Log:
   ../data/processed/removal_log.csv
   31,202 removed entries with reasons

3. Class Weights:
   ../data/processed/class_weights.json
   Normal: 1.2211, Malicious: 0.8467

4. Data Quality Report:
   ../data/processed/data_quality_report.json
   Complete JSON report with all statistics

PHASE 1 DAY 1-2 COMPLETED SUCCESSFULLY

Next Steps:
  Day 3-5: Perform stratified train/val/test split
  Day 6-8: Conduct exploratory data analysis
  Day 9-10: Final validation and documentation
